In [7]:
# Para modelos que se van a ocupar
import torch
from asteroid import ConvTasNet
from asteroid.models import BaseModel

# Para grabar y reproducir audio
import soundfile as sf
from IPython.display import Audio

# Para trabajar con jack-audio
import jack

import sys
import signal
import os
import threading #Para usar hilos
import time
import queue # buena opción para trabajar con hilos 

import argparse


import matplotlib.pyplot as plt
import numpy as np
import sounddevice as sd

In [8]:
# Modelo pre-entrenado DCCRNet
modelP = BaseModel.from_pretrained("JorisCos/DCCRNet_Libri1Mix_enhsingle_16k")

modelP2 = BaseModel.from_pretrained("JorisCos/ConvTasNet_Libri2Mix_sepnoisy_16k")

#Cargamos el modelo ConvTasNet
model1 = torch.load("/home/felix/model3_ConvTasNet.pth")

#Cargamos el modelo LSRMTasNet
model2 = torch.load("/home/felix/model1_LSTMTasNet.pth") 

#Cargamos el modelo SUDO
model3 = torch.load("/home/felix/sudo.pth")

#Cargamos el modelo DPTNET
model4 = torch.load("/home/felix/DPTNET.pth")

#Cargamos el modelo DCCRNet
model5 = torch.load("/home/felix/DCCRNet2.pth")

In [9]:
# Cargamos un audio para probar el modelo
mixture, _ = sf.read("wav_mic1C16.wav", dtype="float32", always_2d=True)
mixture = mixture.transpose()
mixture = mixture.reshape(1, mixture.shape[0], mixture.shape[1])

In [31]:
# Hacemos inferencia con nuestro modelo
inicio = time.time()

out_wavs = model1.separate(mixture, resample = True)

fin = time.time()

print(fin-inicio)

8.324958562850952


In [32]:
# Fuente 1 separada
Audio(out_wavs[0][0][:], rate = 16000)

In [33]:
Audio(out_wavs[0][1][:], rate = 16000)

In [17]:
import queue
import sys
import threading

import jack
import soundfile as sf
from scipy.signal import resample

clientname = "test"
buffersize = 12
filename = 'wav_mic1C.wav'

q = queue.Queue(maxsize=buffersize)

audioS1 = []
audioS2 = []


event = threading.Event()



def resample_audio(audio, orig_sr, target_sr):
    ratio = target_sr / orig_sr
    resampled_audio = resample(audio, int(len(audio) * ratio))
    return resampled_audio


def print_error(*args):
    print(*args, file=sys.stderr)


def xrun(delay):
    print_error("An xrun occured, increase JACK's period size?")


def shutdown(status, reason):
    print_error('JACK shutdown!')
    print_error('status:', status)
    print_error('reason:', reason)
    event.set()


def stop_callback(msg=''):
    if msg:
        print_error(msg)
    for port in client.outports:
        port.get_array().fill(0)
    event.set()
    raise jack.CallbackExit


def fill_buffer():
    
    with sf.SoundFile(filename) as f:
        block_generator = f.blocks(blocksize=blocksize, dtype='float32',
                                   always_2d=True, fill_value=0)
        for _, out_data in zip(range(buffersize), block_generator):
            #out_data.shape (4096, 1)
            q.put_nowait(out_data)  # Pre-fill queue
        for out_data in block_generator:
            q.put(out_data)
        q.put(None)


def process():
    while True:
        try:
            data = q.get()
            if data is None:
                break  # Playback is finished
            mix = data.reshape(1, 1, data.shape[0])
            
            out_wavs = modelP2.separate(mix, resample= True)
            out_data = out_wavs[0][0][:]
            audioS1.append(out_data)
            
            out_data = out_data.reshape(data.shape[0], 1)
            for channel, port in zip(out_data.T, client.outports):
                port.get_array()[:] = channel
        except queue.Empty:
            pass


try:
    client = jack.Client(clientname)
    blocksize = client.blocksize
    samplerate = client.samplerate
    client.set_xrun_callback(xrun)
    client.set_shutdown_callback(shutdown)
    

    with client:
        
        client.outports.register('out_1')
        target_ports = client.get_ports(
            is_physical=True, is_input=True, is_audio=True)
    
        for source, target in zip(client.outports, target_ports):
            source.connect(target)

        fill_thread = threading.Thread(target=fill_buffer)
        fill_thread.start()

        process_thread = threading.Thread(target=process)
        process_thread.start()

        fill_thread.join()
        process_thread.join()

except KeyboardInterrupt:
    print('\nInterrupted by user')
except (queue.Empty):
    # A timeout occured, i.e. there was an error in the callback
    print("Empty Queue") 

JACK shutdown!
status: <jack.Status 0x21: failure, server_error>
reason: JACK server has been closed
Cannot read socket fd = 70 err = Success
CheckRes error
JackSocketClientChannel read fail



Interrupted by user


Server is not running
Server is not running


In [25]:
newArr = []
for arr in audio:
    for i in arr:
        newArr.append(i)
wav2 = np.array(newArr)   

In [26]:
Audio(wav2, rate = 16000)

JackTemporaryException : now quits...
Jack main caught signal 2


Released audio card Audio1
audio_reservation_finish


In [12]:
wav = resample_audio(wav2, 16000, 44100)

In [14]:
Audio(wav, rate = 44100)